In [2]:
from functools import reduce
import numpy as np
import pandas as pd
# set pandas options to display pretty much everything because there is a crazy amount of columns
pd.set_option('display.max_colwidth', -1)
pd.set_option('display.max_columns', None)

In [3]:
xl = pd.ExcelFile('DataDownload.xls')
sheets = xl.sheet_names[2:] # First two sheets are meta data

In [4]:
# sheets that we will merge/join using the FIPS column
merge_sheets = [
     'Supplemental Data - County',
     'ACCESS',
     'STORES',
     'RESTAURANTS',
     'ASSISTANCE',
     'INSECURITY',
     'PRICES_TAXES',
     'LOCAL',
     'HEALTH',
     'SOCIOECONOMIC'
]
# The state sheet only has one row per state, will merge on State column
state_only = 'Supplemental Data - State'

### Data Cleaning issues
- The data was a little too messy overall for simple concatentation along an axis, and I wasn't going to try and verify everthing was accurate, so joining by FIPS seemed like the obvious solution.
- Had to initially leave out the Supplemental State - State sheet because it does not contain county level data.
- The Supplemental Data - State sheet has two cells with '--' as values while the rest are empty in the last row and was causing issues.
- The State column from the Supplemental Data - County sheet had leading and or trailing white space that had to be cleaned to join the Supplemental State data.
- The Supplemental Data - County FIPS column had tailing white space.
- There appear to be 2 counties that ONLY have supplemental data and nothing else. We will most likely want to exclude them from analysis.
- Some of the columns that appear to be numeric have a comma in them. This was causing pandas to read the data as an object.

### Steps/Code explanation
- The dataframes variable is a generator. It behaves like a list, but you can't slice it. It is lazily evaluated. You can only iterate over it once. It is not the fastest way to do this, but now we don't have to hold so much redudant data in memory.
- reduce takes a function and applies it a sequence. Starting with the first sheet, we merge it with the second. This result is then merged with the third sheet, etc. until the end of the sequence.
- There is probably a more efficient way to convert the should-be-numeric columns to an integer data type, but this gets the job done.

In [5]:
dataframes = (pd.read_excel(xl,i).rename({'FIPS ':'FIPS'},axis=1) if i == 'Supplemental Data - County' else
                pd.read_excel(xl,i).drop(['State','County'],axis=1) for i in merge_sheets)
df = reduce(lambda x,y: x.merge(y,on='FIPS',how='left'), dataframes)
df['State'] = df['State'].apply(lambda x: x.strip()) # strip whitespace from the States column to join
states = pd.read_excel(xl,sheet_name=state_only).query("State==State") # NaN's are not equal to anything, so make sure there is a value for states because of that one stupid row
df = df.merge(states,on='State',how='left')
df.head()

FIPS    State    County 2010 Census Population Population Estimate, 2011  \
0  1001  Alabama  Autauga   54,571                 55,255                     
1  1003  Alabama  Baldwin   182,265                186,653                    
2  1005  Alabama  Barbour   27,457                 27,326                     
3  1007  Alabama  Bibb      22,915                 22,736                     
4  1009  Alabama  Blount    57,322                 57,707                     

  Population Estimate, 2012 Population Estimate, 2013  \
0  55,027                    54,792                     
1  190,403                   195,147                    
2  27,132                    26,938                     
3  22,645                    22,501                     
4  57,772                    57,746                     

  Population Estimate, 2014 Population Estimate, 2015  \
0  54,977                    55,035                     
1  199,745                   203,690                    
2  26,763                    26,270                     
3  22,511                    22,561                     
4  57,621                    57,676                     

  Population Estimate, 2016  LACCESS_POP10  LACCESS_POP15  \
0  55,416                    18428.439685   17496.693038    
1  208,563                   35210.814078   30561.264430    
2  25,965                    5722.305602    6069.523628     
3  22,643                    1044.867327    969.378841      
4  57,704                    1548.175559    3724.428242     

   PCH_LACCESS_POP_10_15  PCT_LACCESS_POP10  PCT_LACCESS_POP15  \
0 -5.056026               33.769657          32.062255           
1 -13.204891              19.318473          16.767489           
2  6.067799               20.840972          22.105560           
3 -7.224696               4.559753           4.230324            
4  140.568857             2.700840           6.497380            

   LACCESS_LOWI10  LACCESS_LOWI15  PCH_LACCESS_LOWI_10_15  PCT_LACCESS_LOWI10  \
0  5344.427472     6543.676824     22.439248               9.793530             
1  9952.144027     9886.831137    -0.656270                5.460261             
2  3135.676086     2948.790251    -5.959985                11.420316            
3  491.449066      596.162829      21.307144               2.144661             
4  609.027708      1650.959482     171.081177              1.062468             

   PCT_LACCESS_LOWI15  LACCESS_HHNV10  LACCESS_HHNV15  PCH_LACCESS_HHNV_10_15  \
0  11.991125           664.216487      677.672769      2.025888                 
1  5.424427            1571.779915     1394.162766    -11.300383                
2  10.739667           406.142372      425.144927      4.678792                 
3  2.601627            275.060875      224.388125     -18.422377                
4  2.880150            705.466783      719.931444      2.050367                 

   PCT_LACCESS_HHNV10  PCT_LACCESS_HHNV15  LACCESS_SNAP15  PCT_LACCESS_SNAP15  \
0  3.284786            3.351332            931.935186      4.608749             
1  2.147827            1.905114            950.535290      1.298900             
2  4.135869            4.329378            422.569040      4.303147             
3  3.458580            2.821427            53.818772       0.676710             
4  3.269380            3.336414            175.370338      0.812727             

   LACCESS_CHILD10  LACCESS_CHILD15  LACCESS_CHILD_10_15  PCT_LACCESS_CHILD10  \
0  4822.500269      4616.971480     -4.261872             8.837112              
1  7916.131932      7007.972675     -11.472260            4.343199              
2  940.419327       1031.927776      9.730601             3.425062              
3  249.204753       232.642670      -6.645974             1.087518              
4  384.911607       910.686113       136.596168           0.671490              

   PCT_LACCESS_CHILD15  LACCESS_SENIORS10  LACCESS_SENIORS15  \
0  8.460485             2388.233228        2180.809285         
1 

In [6]:
df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 3142 entries, 0 to 3141
Columns: 326 entries, FIPS to State Population,  2016
dtypes: float64(314), int64(1), object(11)
memory usage: 7.8+ MB


In [7]:
convert_columns = [
    '2010 Census Population',
    'Population Estimate, 2011', 
    'Population Estimate, 2012',
    'Population Estimate, 2013', 
    'Population Estimate, 2014',
    'Population Estimate, 2015', 
    'Population Estimate, 2016',
    'School Breakfast Program participants FY 2011',
    'School Breakfast Program participants, FY 2012',
]

In [8]:
def converter(x):
    if x is np.nan:
        return x
    if type(x) != str:
        return x
    no_comma = x.replace(',','')
    return pd.to_numeric(no_comma, downcast='integer',errors='coerce')

In [9]:
for col in convert_columns:
    df[col] = df[col].apply(converter)

In [10]:
# df.to_csv('Clean_Data.csv',index=False)

In [11]:
# 2 add'l float, 7 add'l int, 9 fewer object
df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 3142 entries, 0 to 3141
Columns: 326 entries, FIPS to State Population,  2016
dtypes: float64(316), int64(8), object(2)
memory usage: 7.8+ MB


In [12]:
# drop all the columns where at least 90% of the data is empty
drop_thresh_col = df.shape[0]*.9
df = df.dropna(thresh=drop_thresh_col, how='all', axis='columns').copy()

In [13]:
# float columns went from 326 to 256.  Int & object unchanged.
df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 3142 entries, 0 to 3141
Columns: 256 entries, FIPS to State Population,  2016
dtypes: float64(246), int64(8), object(2)
memory usage: 6.2+ MB


In [14]:
# drop all the rows where at least 78% of the data is empty which removes 2 rows
drop_thresh_row = df.shape[1]*.78
df = df.dropna(thresh=drop_thresh_row, how='all', axis='index').copy()

In [15]:
df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 3139 entries, 0 to 3141
Columns: 256 entries, FIPS to State Population,  2016
dtypes: float64(246), int64(8), object(2)
memory usage: 6.2+ MB


In [16]:
# non-numeric columns are?
non_num_features = df.columns[df.dtypes == 'object']
non_num_features

Index(['State', 'County'], dtype='object')

In [17]:
non_num_features.isna()

array([False, False])

In [18]:
num_features = df.select_dtypes(exclude='object')
num_features

FIPS  2010 Census Population  Population Estimate, 2011  \
0     1001   54571                   55255                       
1     1003   182265                  186653                      
2     1005   27457                   27326                       
3     1007   22915                   22736                       
4     1009   57322                   57707                       
5     1011   10914                   10722                       
6     1013   20947                   20848                       
7     1015   118572                  117736                      
8     1017   34215                   34006                       
9     1019   25989                   26073                       
10    1021   43643                   43758                       
11    1023   13859                   13610                       
12    1025   25833                   25549                       
13    1027   13932                   13676                       
14    1029   14972                   14976                       
15    1031   49948                   50484                       
16    1033   54428                   54460                       
17    1035   13228                   13193                       
18    1037   11539                   11369                       
19    1039   37765                   38066                       
20    1041   13906                   13903                       
21    1043   80406                   80457                       
22    1045   50251                   50119                       
23    1047   43820                   43207                       
24    1049   71109                   71389                       
25    1051   79303                   80030                       
26    1053   38319                   38227                       
27    1055   104430                  104236                      
28    1057   17241                   17063                       
29    1059   31704                   31734                       
...    ...     ...                     ...                       
3112  55129  15911                   15792                       
3113  55131  131887                  132292                      
3114  55133  389891                  390811                      
3115  55135  52410                   52322                       
3116  55137  24496                   24579                       
3117  55139  166994                  167646                      
3118  55141  74749                   74588                       
3119  56001  36299                   36895                       
3120  56003  11668                   11742                       
3121  56005  46133                   46594                       
3122  56007  15885                   15824                       
3123  56009  13833                   13730                       
3124  56011  7083                    7139                        
3125  56013  40123                   40595                       
3126  56015  13249                   13592                       
3127  56017  4812                    4819                        
3128  56019  8569                    8632                        
3129  56021  91738                   92637                       
3130  56023  18106                   18018                       
3131  56025  75450                   76410                       
3132  56027  2484                    2487                        
3133  56029  28205                   28476                       
3134  56031  8667                    8703                        
3135  56033  29116                   29285                       
3136  56035  10247                   10145                       
3137  56037  43806                   44028                       
3138  56039  21294                   21474                       
3139  56041  21118                   20918                       
3140  56043  8533                    8470      

In [19]:
num_features.median()

FIPS                                                   2.917500e+04
2010 Census Population                                 2.589300e+04
Population Estimate, 2011                              2.584300e+04
Population Estimate, 2012                              2.585600e+04
Population Estimate, 2013                              2.582400e+04
Population Estimate, 2014                              2.569100e+04
Population Estimate, 2015                              2.571800e+04
Population Estimate, 2016                              2.579500e+04
LACCESS_POP10                                          4.097827e+03
LACCESS_POP15                                          4.131026e+03
PCH_LACCESS_POP_10_15                                 -6.283775e-02
PCT_LACCESS_POP10                                      1.968596e+01
PCT_LACCESS_POP15                                      1.919198e+01
LACCESS_LOWI10                                         1.500780e+03
LACCESS_LOWI15                                  

In [20]:
num_features.isna().sum()

FIPS                                                   0 
2010 Census Population                                 0 
Population Estimate, 2011                              0 
Population Estimate, 2012                              0 
Population Estimate, 2013                              0 
Population Estimate, 2014                              0 
Population Estimate, 2015                              0 
Population Estimate, 2016                              0 
LACCESS_POP10                                          0 
LACCESS_POP15                                          18
PCH_LACCESS_POP_10_15                                  25
PCT_LACCESS_POP10                                      0 
PCT_LACCESS_POP15                                      18
LACCESS_LOWI10                                         0 
LACCESS_LOWI15                                         18
PCH_LACCESS_LOWI_10_15                                 26
PCT_LACCESS_LOWI10                                     0 
PCT_LACCESS_LO

In [21]:
num_features = num_features.fillna(num_features.median())

In [22]:
num_features.isna().sum()

FIPS                                                   0
2010 Census Population                                 0
Population Estimate, 2011                              0
Population Estimate, 2012                              0
Population Estimate, 2013                              0
Population Estimate, 2014                              0
Population Estimate, 2015                              0
Population Estimate, 2016                              0
LACCESS_POP10                                          0
LACCESS_POP15                                          0
PCH_LACCESS_POP_10_15                                  0
PCT_LACCESS_POP10                                      0
PCT_LACCESS_POP15                                      0
LACCESS_LOWI10                                         0
LACCESS_LOWI15                                         0
PCH_LACCESS_LOWI_10_15                                 0
PCT_LACCESS_LOWI10                                     0
PCT_LACCESS_LOWI15             

In [23]:
num_features

FIPS  2010 Census Population  Population Estimate, 2011  \
0     1001   54571                   55255                       
1     1003   182265                  186653                      
2     1005   27457                   27326                       
3     1007   22915                   22736                       
4     1009   57322                   57707                       
5     1011   10914                   10722                       
6     1013   20947                   20848                       
7     1015   118572                  117736                      
8     1017   34215                   34006                       
9     1019   25989                   26073                       
10    1021   43643                   43758                       
11    1023   13859                   13610                       
12    1025   25833                   25549                       
13    1027   13932                   13676                       
14    1029   14972                   14976                       
15    1031   49948                   50484                       
16    1033   54428                   54460                       
17    1035   13228                   13193                       
18    1037   11539                   11369                       
19    1039   37765                   38066                       
20    1041   13906                   13903                       
21    1043   80406                   80457                       
22    1045   50251                   50119                       
23    1047   43820                   43207                       
24    1049   71109                   71389                       
25    1051   79303                   80030                       
26    1053   38319                   38227                       
27    1055   104430                  104236                      
28    1057   17241                   17063                       
29    1059   31704                   31734                       
...    ...     ...                     ...                       
3112  55129  15911                   15792                       
3113  55131  131887                  132292                      
3114  55133  389891                  390811                      
3115  55135  52410                   52322                       
3116  55137  24496                   24579                       
3117  55139  166994                  167646                      
3118  55141  74749                   74588                       
3119  56001  36299                   36895                       
3120  56003  11668                   11742                       
3121  56005  46133                   46594                       
3122  56007  15885                   15824                       
3123  56009  13833                   13730                       
3124  56011  7083                    7139                        
3125  56013  40123                   40595                       
3126  56015  13249                   13592                       
3127  56017  4812                    4819                        
3128  56019  8569                    8632                        
3129  56021  91738                   92637                       
3130  56023  18106                   18018                       
3131  56025  75450                   76410                       
3132  56027  2484                    2487                        
3133  56029  28205                   28476                       
3134  56031  8667                    8703                        
3135  56033  29116                   29285                       
3136  56035  10247                   10145                       
3137  56037  43806                   44028                       
3138  56039  21294                   21474                       
3139  56041  21118                   20918                       
3140  56043  8533                    8470      

In [24]:
df_num = num_features

In [25]:
# LP was finding duplicate column names.  I think it's a bug, but good practice to make col names consistent anyway.
# change column names to lower_case_with_underscores
import re

def standardize_name(cname):
    cname = re.sub(r'[-\.]', ' ', cname)
    cname = cname.strip().lower()
    cname = re.sub(r'\s+', '_', cname)
    return cname

df_num.columns = df_num.columns.map(standardize_name)

In [26]:
def standardize_name(cname):
    cname = re.sub(',','', cname)
    cname = cname.strip().lower()
    cname = re.sub(r'\s+','_', cname)
    return cname

df_num.columns = df_num.columns.map(standardize_name)

In [27]:
df_num

fips  2010_census_population  population_estimate_2011  \
0     1001   54571                   55255                      
1     1003   182265                  186653                     
2     1005   27457                   27326                      
3     1007   22915                   22736                      
4     1009   57322                   57707                      
5     1011   10914                   10722                      
6     1013   20947                   20848                      
7     1015   118572                  117736                     
8     1017   34215                   34006                      
9     1019   25989                   26073                      
10    1021   43643                   43758                      
11    1023   13859                   13610                      
12    1025   25833                   25549                      
13    1027   13932                   13676                      
14    1029   14972                   14976                      
15    1031   49948                   50484                      
16    1033   54428                   54460                      
17    1035   13228                   13193                      
18    1037   11539                   11369                      
19    1039   37765                   38066                      
20    1041   13906                   13903                      
21    1043   80406                   80457                      
22    1045   50251                   50119                      
23    1047   43820                   43207                      
24    1049   71109                   71389                      
25    1051   79303                   80030                      
26    1053   38319                   38227                      
27    1055   104430                  104236                     
28    1057   17241                   17063                      
29    1059   31704                   31734                      
...    ...     ...                     ...                      
3112  55129  15911                   15792                      
3113  55131  131887                  132292                     
3114  55133  389891                  390811                     
3115  55135  52410                   52322                      
3116  55137  24496                   24579                      
3117  55139  166994                  167646                     
3118  55141  74749                   74588                      
3119  56001  36299                   36895                      
3120  56003  11668                   11742                      
3121  56005  46133                   46594                      
3122  56007  15885                   15824                      
3123  56009  13833                   13730                      
3124  56011  7083                    7139                       
3125  56013  40123                   40595                      
3126  56015  13249                   13592                      
3127  56017  4812                    4819                       
3128  56019  8569                    8632                       
3129  56021  91738                   92637                      
3130  56023  18106                   18018                      
3131  56025  75450                   76410                      
3132  56027  2484                    2487                       
3133  56029  28205                   28476                      
3134  56031  8667                    8703                       
3135  56033  29116                   29285                      
3136  56035  10247                   10145                      
3137  56037  43806                   44028                      
3138  56039  21294                   21474                      
3139  56041  21118                   20918                      
3140  56043  8533                    8470                       
3141  56045  7208                    7112 

In [28]:
df_num = df_num.drop('pct_obese_adults08', axis=1)

In [29]:
df_num.to_csv('USDA-0.2.csv')

# Feature Selection

In [30]:
# define model inputs (X) and define model target (y)
target = 'pct_obese_adults13'

X = df_num.drop(target, axis=1)
y = df_num[target]

In [31]:
from sklearn.feature_selection import SelectKBest, f_classif

#List 20 features with top Fisher scores
selector = SelectKBest(f_classif, k = 20)

# New dataframe with the selected features for later use in the classifier. 
# fit() method works too, if you want only the feature names and their corresponding scores
X_new = selector.fit_transform(X, y)
names = X.columns.values[selector.get_support()]
scores = selector.scores_[selector.get_support()]
names_scores = list(zip(names, scores))
ns_df = pd.DataFrame(data = names_scores, columns=['Feature_names', 'F_Scores'])

#Sort the dataframe for better visualization
ns_df_sorted = ns_df.sort_values(['F_Scores', 'Feature_names'], ascending = [False, True])
print(ns_df_sorted)

            Feature_names   F_Scores
14  pct_diabetes_adults13  11.791350
13  pct_diabetes_adults08  9.551956 
4   fsrpth09               7.639582 
5   fsrpth14               7.405714 
6   pc_fsrsales07          5.526236 
11  orchard_farms07        5.453368 
3   fsr14                  5.438483 
2   fsr09                  5.433689 
12  orchard_farms12        5.431982 
16  recfac14               5.351683 
7   pc_fsrsales12          5.184877 
15  recfac09               5.178710 
10  fmrkt09                5.002423 
17  pct_nhblack10          4.893021 
9   pct_free_lunch09       4.863516 
0   pct_laccess_black15    4.765218 
8   pc_snapben10           4.703230 
19  povrate15              4.701276 
1   specs14                4.667427 
18  pct_nhasian10          4.641756 


/Applications/anaconda3/lib/python3.7/site-packages/sklearn/feature_selection/univariate_selection.py:114: UserWarning: Features [119] are constant.
  UserWarning)
/Applications/anaconda3/lib/python3.7/site-packages/sklearn/feature_selection/univariate_selection.py:115: RuntimeWarning: invalid value encountered in true_divide
  f = msb / msw


In [32]:
# do not see any attributes to inform which features were selected.  Not suitable for our purposes.

from sklearn.feature_selection import VarianceThreshold

sel = VarianceThreshold(threshold=(.8 * (1-.8)))
sel.fit_transform(X)

array([[1.001000e+03, 5.457100e+04, 5.525500e+04, ..., 4.849377e+06,
        4.858979e+06, 4.863300e+06],
       [1.003000e+03, 1.822650e+05, 1.866530e+05, ..., 4.849377e+06,
        4.858979e+06, 4.863300e+06],
       [1.005000e+03, 2.745700e+04, 2.732600e+04, ..., 4.849377e+06,
        4.858979e+06, 4.863300e+06],
       ...,
       [5.604100e+04, 2.111800e+04, 2.091800e+04, ..., 5.841530e+05,
        5.861070e+05, 5.855010e+05],
       [5.604300e+04, 8.533000e+03, 8.470000e+03, ..., 5.841530e+05,
        5.861070e+05, 5.855010e+05],
       [5.604500e+04, 7.208000e+03, 7.112000e+03, ..., 5.841530e+05,
        5.861070e+05, 5.855010e+05]])

In [34]:
from sklearn.ensemble import RandomForestRegressor
from sklearn.feature_selection import RFECV

# RFECV A supervised learning estimator with a fit method that provides information about feature importance either \
# through a coef_ attribute or through a feature_importances_ attribute

rfsel = RFECV(RandomForestRegressor(), cv=5, n_estimators=100)
rfsel.fit(X, y)

/Applications/anaconda3/lib/python3.7/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/Applications/anaconda3/lib/python3.7/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/Applications/anaconda3/lib/python3.7/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/Applications/anaconda3/lib/python3.7/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/Applications/anaconda3/lib/python3.7/si

KeyboardInterrupt: 

In [50]:
# No train test split.  No CV.
rfsel.score(X, y)

0.9476199776794807

In [51]:
# The number of selected features with cross-validation
rfsel.n_features_

10

In [52]:
# The mask of selected features.
rfsel.support_

array([ True, False, False, False, False, False, False, False, False,
       False, False, False, False, False, False, False, False, False,
       False, False, False, False, False, False, False, False, False,
       False, False, False, False, False, False, False, False, False,
       False, False, False, False, False, False, False, False, False,
       False, False, False, False, False, False, False, False, False,
       False, False, False, False, False, False, False, False, False,
       False, False, False, False, False, False, False, False, False,
       False, False, False, False, False, False, False, False, False,
       False, False, False, False, False, False, False, False, False,
       False, False,  True, False, False,  True, False, False, False,
        True,  True, False, False, False, False, False, False, False,
       False, False, False, False, False, False, False, False, False,
       False, False, False, False, False, False,  True, False, False,
       False, False,

In [90]:
# Index of the top 10 feature ranking descending

rfsel.ranking_[:15]

array([  1, 164, 179, 166, 181,  14, 168, 167, 151, 136, 101, 102, 130,
       133, 138])

In [91]:
# Top 15 feature names, descending where scikit-learn
# RandomForestRegressor was the estimator

X.columns[rfsel.ranking_[:15]]

Index(['2010_census_population', 'pc_dirsales07', 'slhouse12', 'fmrkt09',
       'ghveg_farms07', 'laccess_lowi15', 'fmrktpth09', 'fmrkt16',
       'sodatax_stores14', 'pct_cacfp09', 'redemp_snaps12', 'redemp_snaps16',
       'pct_sfsp09', 'pct_wic09', 'pch_cacfp_09_15'],
      dtype='object')

In [42]:
list(X.columns[rfsel.ranking_[:15]])

AttributeError: 'RFECV' object has no attribute 'ranking_'

In [39]:
from sklearn.linear_model import Lasso

lassel = RFECV(Lasso(alpha=.1), cv=5)
lassel.fit(X, y)
lassel.n_features_

/Applications/anaconda3/lib/python3.7/site-packages/sklearn/linear_model/coordinate_descent.py:492: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Fitting data with very small alpha may cause precision problems.
  ConvergenceWarning)
/Applications/anaconda3/lib/python3.7/site-packages/sklearn/linear_model/coordinate_descent.py:492: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Fitting data with very small alpha may cause precision problems.
  ConvergenceWarning)
/Applications/anaconda3/lib/python3.7/site-packages/sklearn/linear_model/coordinate_descent.py:492: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Fitting data with very small alpha may cause precision problems.
  ConvergenceWarning)
/Applications/anaconda3/lib/python3.7/site-packages/sklearn/linear_model/coordinate_descent.py:492: ConvergenceWarning: Objective did no

47

In [40]:
# Top 15 feature names, descending where scikit-learn
# RandomForestRegressor was the estimator
lassel.ranking_[:15]

array([52, 66, 80, 81, 92, 65, 82, 69, 41, 48, 77,  1,  1, 50, 27])

In [41]:
X.columns[lassel.ranking_[:15]]

Index(['grocpth09', 'pch_convspth_09_14', 'wics12', 'pch_wics_08_12', 'fsr14',
       'convspth14', 'wicspth08', 'pch_specs_09_14', 'laccess_nhasian15',
       'pct_laccess_multir15', 'snapspth16', '2010_census_population',
       '2010_census_population', 'groc14', 'laccess_child_10_15'],
      dtype='object')

In [43]:
list(X.columns[lassel.ranking_[:15]])

['grocpth09',
 'pch_convspth_09_14',
 'wics12',
 'pch_wics_08_12',
 'fsr14',
 'convspth14',
 'wicspth08',
 'pch_specs_09_14',
 'laccess_nhasian15',
 'pct_laccess_multir15',
 'snapspth16',
 '2010_census_population',
 '2010_census_population',
 'groc14',
 'laccess_child_10_15']

In [62]:
from sklearn.linear_model import LassoCV
from sklearn.feature_selection import SelectFromModel

print(X.shape)

lassel = SelectFromModel(LassoCV(cv=5, max_iter=10000, normalize=True))
lassel.fit(X, y)
lassel.transform(X).shape

(3139, 252)


(3139, 22)

In [67]:
lassel.estimator_

LassoCV(alphas=None, copy_X=True, cv=5, eps=0.001, fit_intercept=True,
    max_iter=10000, n_alphas=100, n_jobs=None, normalize=True,
    positive=False, precompute='auto', random_state=None,
    selection='cyclic', tol=0.0001, verbose=False)

In [68]:
lassel.threshold_

1e-05

In [77]:
type(lassel.transform(X))

numpy.ndarray

In [83]:
# no matter what I try I cannot get at the feature names
lassel.transform(X).tolist()

[[0.628059481,
  0.523512952,
  649.5113669582424,
  484.3815070495379,
  0.46221921943258293,
  -0.2710647522054557,
  0.9160899337992502,
  1.055597276711836,
  -0.3,
  8.5,
  6.024096385542169,
  13.110539845758353,
  1.5546918378678511,
  11.4,
  13.0,
  5.0,
  0.073889351,
  0.090260854,
  17.582598816221072,
  11.995382162687141,
  26.777958989206724,
  56580.0],
 [1.125937817,
  1.104387065,
  649.5113669582424,
  484.3815070495379,
  0.46221921943258293,
  -0.2710647522054557,
  0.9160899337992502,
  1.055597276711836,
  -0.3,
  8.5,
  7.023705004389816,
  10.414560161779574,
  0.47801006181673333,
  9.8,
  10.4,
  25.0,
  0.100331093,
  0.124930663,
  9.308424546676543,
  16.771184813321263,
  22.987408443749484,
  52387.0],
 [0.433886539,
  0.55789043,
  649.5113669582424,
  484.3815070495379,
  0.46221921943258293,
  -0.2710647522054557,
  0.9160899337992502,
  1.055597276711836,
  -0.3,
  8.5,
  2.889245585874799,
  2.276707530647986,
  0.012457357506995285,
  13.6,
  18.4,

In [89]:
from sklearn.linear_model import Lasso

mlas = Lasso(alpha=.1, max_iter=1_000_000)
mlas.fit(X, y)
mlas.get_params

/Applications/anaconda3/lib/python3.7/site-packages/sklearn/linear_model/coordinate_descent.py:492: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Fitting data with very small alpha may cause precision problems.
  ConvergenceWarning)


<bound method BaseEstimator.get_params of Lasso(alpha=0.1, copy_X=True, fit_intercept=True, max_iter=1000000,
   normalize=False, positive=False, precompute=False, random_state=None,
   selection='cyclic', tol=0.0001, warm_start=False)>

In [ ]:
mlas.score(X, y)

In [93]:
from sklearn.linear_model import LinearRegression

mlinreg = LinearRegression()
mlinreg.fit(X, y)
mlinreg.get_params()

{'copy_X': True, 'fit_intercept': True, 'n_jobs': None, 'normalize': False}

In [ ]:
mlinreg.score(X, y)

In [35]:
from sklearn.preprocessing import StandardScaler

# instantiate StandardScaler()
scaler = StandardScaler()

# Fit your data on the scaler object
scaled_df = scaler.fit_transform(df_num)
scaled_df = pd.DataFrame(scaled_df, columns=df_num.columns)

/Applications/anaconda3/lib/python3.7/site-packages/sklearn/preprocessing/data.py:625: DataConversionWarning: Data with input dtype int64, float64 were all converted to float64 by StandardScaler.
  return self.partial_fit(X, y)
/Applications/anaconda3/lib/python3.7/site-packages/sklearn/base.py:462: DataConversionWarning: Data with input dtype int64, float64 were all converted to float64 by StandardScaler.
  return self.fit(X, **fit_params).transform(X)
